# Aufgabe 4:

In [2]:
#Import stuff & things
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score
import numpy as np

import pickle
import re
import nltk 

# Support-Functions

In [3]:
#Convenient function to output test items
def show_test_item(clf, i, text=True, classify=True):
    a = 'actual: ' + str(test.iloc[i].recommended)
    p = ''
    if classify:
        p = ' / predicted: ' + str(clf.predict(vectorizer.transform([test.iloc[i].content_text]))[0])
    print('[' + str(i) + '] ' +a + p)
    if text:
        print('\n')
        print(test.iloc[i].content_text)

In [4]:
def raw_tagger(tagger, text):
    sentences = sent_detector.tokenize(text)
    return [tagger.tag(re.findall('(\w+)', sentence)) for sentence in sentences]

   # Input Tagger

In [5]:
path = '/Users/juliusstahnke/Documents/HTW/Analytics/Analytics/Aufgabe4/'
filename = 'classifier-based-german-pos-tagger.pickle'
with open(path + filename, 'rb') as f:
    tagger = pickle.load(f)

In [6]:
sent_detector = nltk.data.load('tokenizers/punkt/german.pickle')

# Read Files

In [7]:
#Read Datasets for all Areas
dir = '/Users/juliusstahnke/Documents/HTW/Analytics/Analytics/Aufgabe4'
games = pd.read_json(dir + '/games/games.json', orient='records', encoding='utf8')
music = pd.read_json(dir + '/music/music.json', orient='records', encoding='utf8')
apps = pd.read_json(dir + '/apps/apps.json', orient='records', encoding='utf8')

# Split in Test and Train

In [8]:
#Set Randomn State
random_state = 100

#Set Traindata for games
train_games_positiv = games[games.recommended==True].sample(frac=0.8, random_state=random_state)
train_games_negativ = games[games.recommended==False].sample(frac=0.8, random_state=random_state)
train_games = pd.concat([train_games_positiv, train_games_negativ])
test_games = games.drop(train_games.index)

#Set Traindata for music
train_music_positiv = music[music.rating.isin(['8', '9', '10', '11', '12', '13', '14', '15'])].sample(frac=0.8, random_state=random_state)
train_music_negativ = music[music.rating.isin(['1', '2', '3', '4', '5', '6', '7'])].sample(frac=0.8, random_state=random_state)
train_music = pd.concat([train_music_positiv, train_music_negativ])
test_music = music.drop(train_music.index)

#Set Traindata for apps
train_apps_positiv = apps[apps.Rating >= 3].sample(frac=0.8, random_state=random_state)
train_apps_negativ = apps[apps.Rating < 3].sample(frac=0.8, random_state=random_state)
train_apps = pd.concat([train_apps_positiv, train_apps_negativ])
test_apps = apps.drop(train_apps.index)

# Normalize Tableformat

In [9]:
#Einfügen positiv Spalte und Text
#games.reset_index(inplace=True)
train_games['Positiv'] = (games.recommended)
train_games['Text'] = (games.content_text)

#Einfügen positiv Spalte und Text
#games.reset_index(inplace=True)
train_games['Positiv'] = (games.recommended)
train_games['Text'] = (games.content_text)

#Einfügen positiv Spalte und Text
train_apps = apps[apps.Rating!=3]
train_apps.reset_index(inplace=True)
train_apps['Positiv'] = (apps.Rating > 3)

#Einfügen positiv Spalte und Text
test_apps = apps[apps.Rating!=3]
test_apps.reset_index(inplace=True)
test_apps['Positiv'] = (apps.Rating > 3)

#Einfügen positiv Spalte und Text
train_music['Text'] = (music.description + music.summary)
train_music.reset_index(inplace=True)
train_music['Positiv'] = (music.rating.isin(['8', '9', '10', '11', '12', '13', '14', '15']))

#Einfügen positiver Spalten und Texte
test_music['Text'] = (music.description + music.summary)
test_music.reset_index(inplace=True)
test_music['Positiv'] = (music.rating.isin(['8', '9', '10', '11', '12', '13', '14', '15']))

/Users/juliusstahnke/miniconda3/lib/python3.5/site-packages/ipykernel/__main__.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
/Users/juliusstahnke/miniconda3/lib/python3.5/site-packages/ipykernel/__main__.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


# Vectorizer Games untagged

In [10]:
#Vectorizer Games
vectorizer = CountVectorizer(min_df=10, max_df=200, token_pattern='\w+')
vectorizer.fit(train_games.content_text)

X = vectorizer.transform(train_games.content_text)
y = train_games.recommended
clf = MultinomialNB().fit(X, y)
actuals = test_games.recommended
predicted = clf.predict(vectorizer.transform(test_games.content_text))
accuracy_score(actuals, predicted)

0.75987306064880111

# Tag Games

In [11]:
train_games_tagged = [raw_tagger(tagger, a) for a in train_games.content_text]

train_games_tagged

#PICKLE THE RESULT OF THIS STEP! THIS RUNS FOREVER!
#Here is how you pickle something:
#with open('games_pos_tagged.pickle', 'wb') as fp:
#    pickle.dump(train_games_tagged, fp)
    
#If you want to load your pickled stuff use the following: 
#with open('games_pos_tagged.pickle', 'rb') as fp: 
#    test = pickle.load(fp)

[[[('Der', 'ART'),
   ('absolut', 'ADJD'),
   ('beste', 'ADJA'),
   ('Teil', 'NN'),
   ('der', 'ART'),
   ('Serie', 'NN')],
  [('Hab', 'NE'),
   ('zuvor', 'ADV'),
   ('Fallout', 'NE'),
   ('3', 'CARD'),
   ('und', 'KON'),
   ('New', 'NE'),
   ('Vegas', 'NE'),
   ('regelrecht', 'ADJD'),
   ('gesuchtet', 'VVPP'),
   ('aber', 'KON'),
   ('keins', 'VMFIN'),
   ('der', 'ART'),
   ('Spiele', 'NN'),
   ('hat', 'VAFIN'),
   ('mich', 'PPER'),
   ('bisher', 'ADV'),
   ('so', 'ADV'),
   ('sehr', 'ADV'),
   ('gefesselt', 'VVPP')],
  [('Fallout', 'NE'),
   ('3', 'CARD'),
   ('hatte', 'VAFIN'),
   ('die', 'ART'),
   ('besseren', 'ADJA'),
   ('DLCs', 'NN'),
   ('bisher', 'ADV')],
  [('In', 'APPR'),
   ('Fallout', 'NE'),
   ('4', 'CARD'),
   ('erkennt', 'VVFIN'),
   ('man', 'PIS'),
   ('viele', 'PIAT'),
   ('erfolgreiche', 'ADJA'),
   ('und', 'KON'),
   ('bekannte', 'VVFIN'),
   ('Mods', 'NE'),
   ('aus', 'PTKVZ'),
   ('3', 'CARD'),
   ('und', 'KON'),
   ('NV', 'NN'),
   ('welchr', 'VAFIN'),
   ('dire

# Filter for Adjectives

In [14]:
#Declare result variabe
result_games_adja = []

#For every document (Needed because Reviews Contain more than one Sentence)
for document in train_games_tagged: 
    result_doc = ""
    #Check in Every Sentence (Needed Because Senteces have more than one word)
    for sentence in document:
        result_sen = ""
        #Check if the Second Element of the Wordtupel fullfills Condition
        for word in sentence:
            if word[1] == 'ADJA':
                #If so add it to Sentence, else dont
                result_sen = result_sen + " " + word[0]
        #If Sentence contains words that fullfill Condition add it to document, else dont 
        if len(result_sen) != 0:        
            result_doc = result_doc + result_sen
    #Add Document to Result (No Check if emty because we want reprensentation for every review in Trainingsdata)
    result_games_adja.append(result_doc)

result_games_adja 

[' beste besseren erfolgreiche rachsüchtigen beiseite anbleibende gute klare',
 ' hübsche welche verwahrlostes Bewegen ducken einfacher leichtere gleichartige cheaten',
 ' typisches fremden urzeitlichen entsprechende entsprechenden bestimmten größeren meiste einheimischen bedrohungen verschiedene',
 '',
 '',
 ' besten harte krankes anderen anstecken allgemeine steuerung andere anderen zufuß größeren gekennzeichneten mehrfaches oberriesiges wichtiges dergleichen selbe Deadline ganzen bekanntes netten ganze herumliegenden gute',
 ' anderen guten anderen einzelne einigermaßen Weiteren bequemen einzige gelungenes großen mittleren starke neuer',
 ' andere richtige beeinflussen positiven negativen richtige hineinzuversetzen hineinversetzen unglaublichen welches gute',
 ' gutes',
 '',
 ' größten lebenden unangefochtenen hunderte entwickelten fortgeschrittene erste kleiner nettem tapferere kleine beliebten frühen 90er bekannten unterschiedliche Geheimgängen x ten alten intuitive moderne eigene

## Vectorize for filtert adjectives

In [22]:
#Vectorizer Games
vectorizer = CountVectorizer(min_df=10, max_df=200, token_pattern='\w+')
vectorizer.fit(result_games_adja)

X = vectorizer.transform(result_games_adja)
y = train_games.recommended
clf = MultinomialNB().fit(X, y)
actuals = test_games.recommended
predicted = clf.predict(vectorizer.transform(test_games.content_text))
accuracy_score(actuals, predicted)

0.55835684062059243

# Filter for Adjectivs, adverbs, nouns and verbs

In [27]:
#Declare result variabe
result_games_multiple = []

#For every document (Needed because Reviews Contain more than one Sentence)
for document in train_games_tagged: 
    result_doc = ""
    #Check in Every Sentence (Needed Because Senteces have more than one word)
    for sentence in document:
        result_sen = ""
        #Check if the Second Element of the Wordtupel fullfills Condition
        for word in sentence:
            if word[1] == 'ADJA' or word[1] == 'ADV' or word[1] == 'NN' or 'VV' in word[1]:
                #If so add it to Sentence, else dont
                result_sen = result_sen + " " + word[0]
        #If Sentence contains words that fullfill Condition add it to document, else dont 
        if len(result_sen) != 0:        
            result_doc = result_doc + result_sen
    #Add Document to Result (No Check if emty because we want reprensentation for every review in Trainingsdata)
    result_games_multiple.append(result_doc)

result_games_multiple

[' beste Teil Serie zuvor gesuchtet Spiele bisher so sehr gefesselt besseren DLCs bisher erkennt erfolgreiche bekannte NV Spiel integriert bauen Negativpunkt ansehen Tatsache dass Hauptcharakter diesmal Namen Stimme besitzt finde aber Fall gefällt sogar Namenlosen rachsüchtigen spielen Jetzt spielt rachsüchtigen Namen Etwas verarscht kam aber doch CD Version da nur etwa befinden aber nunmal CD da BlueRay benutzen beiseite Spiel sehr Vorgänger Sehr begrüßen immernoch anbleibende gute seitens Punkt Spiel erreicht Mods installieren Spiel crasht installieren gebe Spiel klare Bewertung noch Fall kaufen',
 ' Trailern bekommt ja Gefühl Spiel geht hübsche Insel Open erkundet erspielt Kauf dann doch noch Liebe Detail Kreativität überrascht Zeichnen Linien basieren welche Vielfalt Hinweisen existieren unbedingt zwar immer wieder Insel selbst wirkt Nebeneinander Minimalismus absurden Details fundiert Locations verwahrlostes Gebäude spiele spiele lieber Window Auflösung vermutlich Einstellungen gi

# Vectorize for Adjectivs, adverbs, nouns and verbs

In [28]:
#Vectorizer Games
vectorizer = CountVectorizer(min_df=10, max_df=200, token_pattern='\w+')
vectorizer.fit(result_games_multiple)

X = vectorizer.transform(result_games_multiple)
y = train_games.recommended
clf = MultinomialNB().fit(X, y)
actuals = test_games.recommended
predicted = clf.predict(vectorizer.transform(test_games.content_text))
accuracy_score(actuals, predicted)

0.71738363892806767

# Vectorize Apps Untagged

In [ ]:
#Vectorizer Games
vectorizer = CountVectorizer(min_df=10, max_df=200, token_pattern='\w+')
vectorizer.fit(train_games.content_text)

X = vectorizer.transform(train_games.content_text)
y = train_games.recommended
clf = MultinomialNB().fit(X, y)
actuals = test_games.recommended
predicted = clf.predict(vectorizer.transform(test_games.content_text))
accuracy_score(actuals, predicted)